## 중첩분석(Overlay/ Overlap)
앞서 배운 공간조인(sjoin 등) 기법을 이용하면 서울시 행정동 중에서 지하철역 포인트가 위치한 행정동을 찾아볼 수 있습니다.     
중첩분석은 2개의 (폴리곤) 레이어를 중첩시킨 (폴리곤) 레이어를 만들 수 있는 기법입니다.   
http://wiki.gis.com/wiki/index.php/Overlay   
https://enterprise.arcgis.com/ko/portal/latest/use/geoanalytics-overlay-layers.htm

아래의 분석 과정을 참조하여 서울시의 구 영역과 상권영역 폴리곤을 중첩해보겠습니다.   
https://foss4g.tistory.com/1832?category=601228 

### 패키지 불러오기

In [1]:
import pandas as pd
import geopandas as gpd
#from fiona.crs import from_epsg # 좌표변환 

c:\Users\thlee\AppData\Local\Programs\Python\Python39\lib\site-packages\geopandas\_compat.py:123: UserWarning: The Shapely GEOS version (3.10.1-CAPI-1.16.0) is incompatible with the GEOS version PyGEOS was compiled with (3.10.3-CAPI-1.16.1). Conversions between both will be slow.
  warnings.warn(


### 데이터 로딩

In [2]:
# 서울시 구 행정구역 폴리곤 
gu_gdf = gpd.read_file('data/shp/LARD_ADM_SECT_SGG_11.shp', encoding='cp949')
gu_gdf.head(2)

ADM_SECT_C SGG_NM  SGG_OID COL_ADM_SE  GID  \
0      11740    강동구      337      11740  127   
1      11710    송파구     1969      11710  128   

                                            geometry  
0  POLYGON ((969713.132 1948846.288, 969692.451 1...  
1  POLYGON ((968640.372 1944982.492, 968640.957 1...

서울시 상권영역 데이터    
https://data.seoul.go.kr/dataList/OA-15560/S/1/datasetView.do

In [3]:
# 서울시 상권영역 폴리곤 
tarea_gdf = gpd.read_file('data/shp/TBGIS_TRDAR_RELM.shp')
tarea_gdf.head(2)

STDR_YM_CD TRDAR_SE_C TRDAR_SE_1 TRDAR_NO     TRDAR_NM  XCNTS_VALU  \
0     202112          A       골목상권  2110753  시흥동 은행나무사거리    191934.0   
1     202112          A       골목상권  2110427   노원 을지대학교병원    206265.0   

   YDNTS_VALU SIGNGU_CD ADSTRD_CD  \
0    438813.0     11545  11545710   
1    459431.0     11350  11350611   

                                            geometry  
0  POLYGON ((192008.560 438553.170, 191987.740 43...  
1  POLYGON ((206296.880 459321.710, 206238.710 45...

In [4]:
# 좌표계 확인 - 좌표계가 무엇인지 알 수 있는지요?
tarea_gdf.crs 

<Derived Projected CRS: PROJCS["Korea_2000_Korea_Central_Belt",GEOGCS["GCS ...>
Name: Korea 2000 / Central Belt
Axis Info [cartesian]:
- [east]: Easting (metre)
- [north]: Northing (metre)
Area of Use:
- undefined
Coordinate Operation:
- name: unnamed
- method: Transverse Mercator
Datum: Geocentric datum of Korea
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

In [5]:
# 좌표계가 무엇인지 알 수 있는지요? EPSG Code로는 무엇인지요?  
print(tarea_gdf.crs )

PROJCS["Korea_2000_Korea_Central_Belt",GEOGCS["GCS_Korea_2000",DATUM["D_Korea_2000",SPHEROID["GRS_1980",6378137,298.257222101]],PRIMEM["Greenwich",0],UNIT["Degree",0.0174532925199433]],PROJECTION["Transverse_Mercator"],PARAMETER["latitude_of_origin",38],PARAMETER["central_meridian",127],PARAMETER["scale_factor",1],PARAMETER["false_easting",200000],PARAMETER["false_northing",500000],UNIT["Meter",1],AXIS["Easting",EAST],AXIS["Northing",NORTH]]


In [6]:
# 상권영역을 5179로 변환합니다. 
tarea_gdf5179 = tarea_gdf.to_crs(5179)

## 중첩(Overlay)    
Geopandas의 Overlay를 이용하면 쉽게 중첩을 할 수 있습니다.    
https://geopandas.org/en/stable/docs/reference/api/geopandas.overlay.html 

In [7]:
# 중첩 
result_gdf = gpd.overlay(tarea_gdf5179, gu_gdf, how='union', make_valid=True)
result_gdf.head()

C:\Users\thlee\AppData\Local\Temp\ipykernel_29604\2692232294.py:2: UserWarning: `keep_geom_type=True` in overlay resulted in 72 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  result_gdf = gpd.overlay(tarea_gdf5179, gu_gdf, how='union', make_valid=True)


STDR_YM_CD TRDAR_SE_C TRDAR_SE_1 TRDAR_NO     TRDAR_NM  XCNTS_VALU  \
0     202112          A       골목상권  2110753  시흥동 은행나무사거리    191934.0   
1     202112          A       골목상권  2110755     동일여자고등학교    192300.0   
2     202112          A       골목상권  2110739   시흥3동 우편취급국    191289.0   
3     202112          A       골목상권  2110734        금천파출소    191061.0   
4     202112          A       골목상권  2110751        난곡중학교    191810.0   

   YDNTS_VALU SIGNGU_CD ADSTRD_CD ADM_SECT_C SGG_NM  SGG_OID COL_ADM_SE  \
0    438813.0     11545  11545710      11545    금천구     33.0      11545   
1    439070.0     11545  11545680      11545    금천구     33.0      11545   
2    438014.0     11545  11545690      11545    금천구     33.0      11545   
3    439380.0     11545  11545670      11545    금천구     33.0      11545   
4    442086.0     11545  11545630      11545    금천구     33.0      11545   

     GID                                           geometry  
0  134.0  POLYGON ((947764.017 1938728.924, 947689.358 1...  
1  134.0  POLYGON ((948286.413 1939177.523, 948299.491 1...  
2  134.0  POLYGON ((947144.614 1938063.647, 947072.733 1...  
3  134.0  POLYGON ((946806.772 1939510.320, 946737.079 1...  
4  134.0  POLYGON ((947477.574 1942086.030, 947450.761 1...

In [9]:
result_gdf.explore('TRDAR_SE_1', categorical=True, tiles='http://mt0.google.com/vt/lyrs=y&hl=en&x={x}&y={y}&z={z}&s=Ga', attr='google')

#### 공간현상(상권영역 등)이 공간기준영역(행정구역/ 격자 등)별로 차지하는 면적 또는 면적의 비율을 구할 때 Overlay가 필요합니다. 
#### 다음의 집계(groupby) 과정을 통해서 구별-상권유형별 면적 집계를 구해보겠습니다.      



## 수고 많으셨습니다!!!